# Klonování Darknetu
Následující buňky kódu zkopírují darknet z velmi známeho uložiště AlexeyAB. Dále se zde upravují soubor Makefile kvůli podpoře OPENCV a práci s GPU pro darknet. Náslesledně je spuštěna funkce !make, která inicializuje darknet a vytvoří darknet.exe (darknet).


In [0]:
# Klonování darknetu
!git clone https://github.com/AlexeyAB/darknet

In [0]:
# změny v Makefile pro podporu OPENCV a práce s GPU
%cd darknet
!sed -i 's/OPENCV=0/OPENCV=1/' Makefile
!sed -i 's/GPU=0/GPU=1/' Makefile
!sed -i 's/CUDNN=0/CUDNN=1/' Makefile

In [0]:
# inicializace darknetu (build darknet)
!make

# Připojení Colabu na Drive
V následujícím kódu se připojíme na drive za pomoci vygenerovaného kódu v odkazu.
Následně přiřadíme symbolický link, abychom do "MY\ Drive/" jednoduše přistupovali pomocí "/mydrive".

In [0]:
%cd ..
from google.colab import drive
drive.mount('/content/gdrive')

In [0]:
!ln -s /content/gdrive/My\ Drive/ /mydrive
!ls /mydrive

# Získání dat pro učení z Google Drive
Nyní stáhneme z Google Drive zazipované obrázky a rozbalíme je do složky data.


In [0]:
# Zkopírování zazipovaných obrázků
!cp /mydrive/yolov3/obj.zip ../

In [0]:
# Rozbalení zazipovaných obrázků do složky /darknet/data/obj
!unzip ../obj.zip -d /content/darknet/data

Nahrání souboru yolov3.cfg na Google Drive pro úpravu.

In [0]:
# Nahrání souboru na Google Drive
!cp cfg/yolov3.cfg /mydrive/yolov3/yolov3_custom.cfg

Nahrání upraveného souboru yolov3_custom.cfg, který obsahuje strukturu sítě.

In [0]:
# Nahrání souboru yolov3_custom.cfg z Google Drive
!cp /mydrive/yolov3/yolov3_custom.cfg /content/darknet/cfg

Nahrání vytvořených souborů obj.names a obj.data. z Google Drive

In [0]:
# Nahrání souborů obj.names a obj.data z Google Drive
!cp /mydrive/yolov3/obj.names /content/darknet/data
!cp /mydrive/yolov3/obj.data  /content/darknet/data


Přechod do složky Darknet a nahrání souboru generate_train.py. 

In [0]:
%cd darknet/

In [0]:
# Nahrání souboru generate_train.py z  Google Drive
!cp /mydrive/yolov3/generate_train.py ./

In [0]:
# Spuštění scriptu generate_train.py, který vytvoří soubor train.txt, ten obsahuje relativní cesty k našim trénovacím datům. 
!python generate_train.py

# Stáhnutí předtrénovaných vah
Nyní je třeba stáhnout předtrénované váhy pro YOLOv3 CNN. 


In [0]:
# Stáhnutí vah
!wget http://pjreddie.com/media/files/darknet53.conv.74

# Trénování YOLOv3
Nyní se pomocí následujícího kódu natrénuje YOLOv3. 
Parametr dont_show zde zajišťuje, aby se neukazoval graf učení. Google Colab možnost otevírat obrázky i za chodu kódu nepodporuje.


In [0]:
# train your custom detector
!./darknet detector train data/obj.data cfg/yolov3_custom.cfg darknet53.conv.74 -dont_show

Pokud se trénování z nějakého důvodu přeruší, využijeme k trénování následující kód, který naváže na předešlou práci.

In [0]:
!./darknet detector train data/obj.data cfg/yolov3_custom.cfg /mydrive/yolov3/backup/yolov3_custom_last.weights -dont_show

# Detekce obrazu
Po natrénování vah zkusíme predikovat na několika obrázcích.

In [0]:
# Nastavení souboru yolov3_custom.cfg do testovacího módu
%cd cfg
!sed -i 's/batch=64/batch=1/' yolov3_custom.cfg
!sed -i 's/subdivisions=16/subdivisions=1/' yolov3_custom.cfg
%cd ..


In [0]:
# Detekce objektů na obrázku z Google Drive, výsledek se uloží do složky Darknet pod jménem prediction.jpg
!./darknet detector test data/obj.data cfg/yolov3_custom.cfg /mydrive/yolov3/backup/yolov3_custom_last.weights /mydrive/images/pomstul.jpg -thresh 0.8
imShow('predictions.jpg')

In [0]:
# Stáhnutí predikovaného obrázku na Google Drive
!cp predictions.jpg /mydrive/images/pomstul80tresh.jpg